In [ ]:
#data preprocessing 

In [1]:
import pyspark as ps
from pyspark import SparkContext
from pyspark import SQLContext
from pyspark import SparkConf
from pyspark.ml.feature import Tokenizer, HashingTF, IDF
from pyspark.ml import Pipeline
from pyspark.sql.session import SparkSession
import sys
from os import path
import re


In [2]:
sc = SparkContext.getOrCreate(SparkConf().setMaster("local[*]"))
sql_context = ps.sql.SQLContext(sc)

In [6]:
#Training Set
data = sc.wholeTextFiles('..\\dataset\\data\\train') #sys.argv[1]
data.take(1)

[('file:/C:/Users/Jayant/Documents/sem2/dsp/Project1/sabayon-p1/dataset/data/train/02MRILoE6rNhmt7FUi45.bytes',
  '00401000 C7 01 94 E3 40 00 E9 CE 17 00 00 CC CC CC CC CC\r\n00401010 56 8B F1 C7 06 94 E3 40 00 E8 BB 17 00 00 F6 44\r\n00401020 24 08 01 74 09 56 E8 43 18 00 00 83 C4 04 8B C6\r\n00401030 5E C2 04 00 CC CC CC CC CC CC CC CC CC CC CC CC\r\n00401040 33 C0 C2 10 00 CC CC CC CC CC CC CC CC CC CC CC\r\n00401050 8B 44 24 04 A3 D4 F1 64 00 8B 51 6C 2B 51 64 8A\r\n00401060 41 78 89 51 60 2A 05 C8 F1 64 00 88 41 7B B8 01\r\n00401070 00 00 00 C2 04 00 CC CC CC CC CC CC CC CC CC CC\r\n00401080 A1 D4 F1 64 00 56 8B F1 85 C0 74 16 8B 4C 24 0C\r\n00401090 8B 54 24 08 51 52 FF D0 C7 05 D4 F1 64 00 00 00\r\n004010A0 00 00 8B 46 6C 03 05 C4 F1 64 00 C6 46 7A 69 89\r\n004010B0 46 70 B8 F6 FF FF FF 5E C2 08 00 CC CC CC CC CC\r\n004010C0 56 6A 40 8B F1 8B 46 74 23 05 C4 F1 64 00 68 00\r\n004010D0 10 00 00 68 56 80 20 00 6A 00 89 46 6C FF 15 20\r\n004010E0 E2 40 00 8B 4C 24 08 89 01 8A 56 7A 

In [7]:
#using Saed's method
filenames = open('../dataset/files/X_small_train.txt').read().split('\n')
labels = open('../dataset/files/y_small_train.txt').read().split('\n')
filename_label_dict = {}
for filename, label in zip(filenames, labels):
    filename_label_dict[filename] = label

broadcast_filename_label_dict = sc.broadcast(filename_label_dict)

In [8]:
def pre_process(x):
    fname = x[0].split('/')[-1][:-6]
    label = int(broadcast_filename_label_dict.value[fname])
    word_list = list(filter(lambda x: len(x)==2 and x!='??', re.split('\r\n| ', x[1])))
    return (fname, label, word_list)

In [10]:

#Convert Training Data into a Data Frame
train_data = data.map(lambda x:pre_process(x))
train_data.take(1)[0]
# print('non labeled RDD\'s count :'+ str(train_data.count()))
# train_data = train_data.map(lambda x: append_train_label(x))
# train_data.take(2)
# train_df = train_data.toDF(['id', 'text', 'label'])
# train_df = train_data.toDF(['id','text'])
# print('data frame count.. non labeled too: '+train_df.count() +','+ len(train_df.columns))



('02MRILoE6rNhmt7FUi45',
 2,
 ['C7',
  '01',
  '94',
  'E3',
  '40',
  '00',
  'E9',
  'CE',
  '17',
  '00',
  '00',
  'CC',
  'CC',
  'CC',
  'CC',
  'CC',
  '56',
  '8B',
  'F1',
  'C7',
  '06',
  '94',
  'E3',
  '40',
  '00',
  'E8',
  'BB',
  '17',
  '00',
  '00',
  'F6',
  '44',
  '24',
  '08',
  '01',
  '74',
  '09',
  '56',
  'E8',
  '43',
  '18',
  '00',
  '00',
  '83',
  'C4',
  '04',
  '8B',
  'C6',
  '5E',
  'C2',
  '04',
  '00',
  'CC',
  'CC',
  'CC',
  'CC',
  'CC',
  'CC',
  'CC',
  'CC',
  'CC',
  'CC',
  'CC',
  'CC',
  '33',
  'C0',
  'C2',
  '10',
  '00',
  'CC',
  'CC',
  'CC',
  'CC',
  'CC',
  'CC',
  'CC',
  'CC',
  'CC',
  'CC',
  'CC',
  '8B',
  '44',
  '24',
  '04',
  'A3',
  'D4',
  'F1',
  '64',
  '00',
  '8B',
  '51',
  '6C',
  '2B',
  '51',
  '64',
  '8A',
  '41',
  '78',
  '89',
  '51',
  '60',
  '2A',
  '05',
  'C8',
  'F1',
  '64',
  '00',
  '88',
  '41',
  '7B',
  'B8',
  '01',
  '00',
  '00',
  '00',
  'C2',
  '04',
  '00',
  'CC',
  'CC',
  'CC',
  '

In [12]:
input_label_df = sql_context.createDataFrame(train_data, ['doc', 'label', 'text'])
input_label_df.show(n=2)
#not able to run df.show for n=10 or more??

+--------------------+-----+--------------------+
|                 doc|label|                text|
+--------------------+-----+--------------------+
|02MRILoE6rNhmt7FUi45|    2|[C7, 01, 94, E3, ...|
|05IXcWGxvnkto4sq17zZ|    2|[C7, 00, 44, 79, ...|
+--------------------+-----+--------------------+
only showing top 2 rows



In [13]:
from pyspark.ml.classification import LinearSVC, OneVsRest
from pyspark.ml.evaluation import MulticlassClassificationEvaluator
from pyspark.ml.feature import *
from pyspark.ml import Pipeline

In [15]:

hashingTF = HashingTF(inputCol="text", outputCol="features", numFeatures=256)
hashedTF=hashingTF.transform(input_label_df)

hashedTF.show(n=2)
#not able to run df.show for n=10 or more??

# #ML Pipeline Model
# pipeline = Pipeline(stages=[remover, ngram, hashingTF,lsvc, ovr,ovrModel])


+--------------------+-----+--------------------+--------------------+
|                 doc|label|                text|            features|
+--------------------+-----+--------------------+--------------------+
|02MRILoE6rNhmt7FUi45|    2|[C7, 01, 94, E3, ...|(256,[0,3,4,8,9,1...|
|05IXcWGxvnkto4sq17zZ|    2|[C7, 00, 44, 79, ...|(256,[0,3,4,8,9,1...|
+--------------------+-----+--------------------+--------------------+
only showing top 2 rows



In [ ]:
hashedTF.show(n=10)

In [16]:
(train, test) = hashedTF.randomSplit([0.8, 0.2])
lsvc = LinearSVC(maxIter=5, regParam=0.1)
ovr = OneVsRest(classifier=lsvc)
ovrModel = ovr.fit(train)


Py4JJavaError: An error occurred while calling o364.collectToPython.
: org.apache.spark.SparkException: Job aborted due to stage failure: Task 1 in stage 16.0 failed 1 times, most recent failure: Lost task 1.0 in stage 16.0 (TID 35, localhost, executor driver): java.net.SocketException: Connection reset by peer: socket write error
	at java.net.SocketOutputStream.socketWrite0(Native Method)
	at java.net.SocketOutputStream.socketWrite(SocketOutputStream.java:111)
	at java.net.SocketOutputStream.write(SocketOutputStream.java:155)
	at java.io.BufferedOutputStream.write(BufferedOutputStream.java:122)
	at java.io.DataOutputStream.write(DataOutputStream.java:107)
	at java.io.FilterOutputStream.write(FilterOutputStream.java:97)
	at org.apache.spark.api.python.PythonRDD$.writeUTF(PythonRDD.scala:393)
	at org.apache.spark.api.python.PythonRDD$.org$apache$spark$api$python$PythonRDD$$write$1(PythonRDD.scala:213)
	at org.apache.spark.api.python.PythonRDD$$anonfun$writeIteratorToStream$1.ap

In [ ]:

evaluator = MulticlassClassificationEvaluator(metricName="accuracy")
# compute the classification error on test data.
accuracy = evaluator.evaluate(predictions)
print("Test Error = %g" % (1.0 - accuracy))
